In [17]:
import openmc
import numpy as np
from numpy import pi
from scipy.constants import convert_temperature
import lbh15 
import pandas
import openmc_tally_unit_converter as otuc
import openmc_source_plotter

In [18]:
plomb=openmc.Material(name='plomb')
plomb.add_element('Pb',100)
plomb.set_density('g/cm3',11)

air=openmc.Material(name='air')
air.add_element('N',80)
air.add_element('O',20)
air.set_density('g/cm3',1.3e-3)

beton=openmc.Material(name='beton')
beton.add_element('O',60)
beton.add_element('Si',20)
beton.add_element('C',20)
beton.set_density('g/cm3',2)

materials = openmc.Materials()
materials = openmc.Materials([plomb, air, beton])
materials.export_to_xml()

In [19]:
# geometry
Xm  = openmc.XPlane( x0=-300, name='X-', boundary_type='vacuum')
Xp  = openmc.XPlane( x0=+300, name='X+', boundary_type='vacuum')
Ym  = openmc.YPlane( y0=-200, name='Y-', boundary_type='vacuum')
Yp  = openmc.YPlane( y0=+450, name='Y+', boundary_type='vacuum')

mur_int=openmc.YPlane( y0=+200, name='Mur_int')
mur_ext=openmc.YPlane( y0=+250, name='Mur_ext')

Bottom= openmc.ZPlane(z0= 0, boundary_type='vacuum')
Top= openmc.ZPlane(z0= 300, boundary_type='vacuum')



# Create root Universe
root_universe = openmc.Universe(universe_id=0, name='root universe')

# Create first zone
source_cell = openmc.Cell(name='source et fill')
source_cell.fill = air 
source_cell.region =  -Top & +Bottom & -mur_int & +Xm & +Ym & -Xp
root_universe.add_cell(source_cell)

# Create wall
wall_cell = openmc.Cell(name='wall')
wall_cell.fill = beton
wall_cell.region =  -Top & +Bottom & -mur_ext & +Xm & +mur_int & -Xp
root_universe.add_cell(wall_cell)

#create air for tallies
air_dect_cell = openmc.Cell(name='air_dect')
air_dect_cell.fill = air
air_dect_cell.region =   -Top & +Bottom & -Yp & +Xm & +mur_ext & -Xp
root_universe.add_cell(air_dect_cell)

# Create Geometry and set root Universe
geometry = openmc.Geometry(root_universe)

# Export to "geometry.xml"
geometry.export_to_xml()



In [20]:
mesh_r = openmc.RegularMesh()
mesh_r.dimension = [1, 1, 1]
mesh_r.lower_left  = [-20, 80, 130]
mesh_r.upper_right = [+20, 120, 170]
mesh_filter_r = openmc.MeshFilter(mesh_r)

mesh_a1m = openmc.SphericalMesh()
mesh_a1m.origin = [0,100,150]
mesh_a1m.r_grid = [0,25.]
mesh_a1m_filter = openmc.MeshFilter(mesh_a1m)


mesh_global = openmc.RegularMesh()
mesh_global.dimension = [8, 17, 6]
mesh_global.lower_left  = [-200, -200, 0]
mesh_global.upper_right = [+200, 450, 300]
mesh_filter_global = openmc.MeshFilter(mesh_global)

# energy_filter_g = openmc.EnergyFilter([0,1e3,5e4,1e5,2e5,3e5,4e5,6e5,8e5,1e6,1.33e6,1.67e6,2e6,2.5e6,3e6,4e6,5e6,6.5e6,8e6,1e7,2e7])
phot_filter = openmc.ParticleFilter('photon')
# these are the dose coefficients coded into openmc
# originally from ICRP https://journals.sagepub.com/doi/10.1016/j.icrp.2011.10.001
energy_bins_g, dose_coeffs_g = openmc.data.dose_coefficients(
    particle="photon",
    geometry="ISO",  # we are using the ISO direction as this is a dose field with dose
)
energy_function_filter_g = openmc.EnergyFunctionFilter(energy_bins_g, dose_coeffs_g)
energy_function_filter_g.interpolation = "cubic"  # cubic interpolation is recommended by ICRP


# Instantiate an empty Tallies object
tallies = openmc.Tallies()



# gamma fluxes
tallya1mg = openmc.Tally(name='flux g avant 1m')
tallya1mg.filters = [mesh_a1m_filter,phot_filter]
tallya1mg.scores = ['flux']
tallies.append(tallya1mg)

tallya1mgr = openmc.Tally(name='flux g avant 1m R')
tallya1mgr.filters = [mesh_filter_r,phot_filter]
tallya1mgr.scores = ['flux']
tallies.append(tallya1mgr)


mesh_globalg = openmc.Tally(name='flux g global')
mesh_globalg.filters = [mesh_filter_global,phot_filter]
mesh_globalg.scores = ['flux']
tallies.append(mesh_globalg)

# gamma doses
tallyaD1mg = openmc.Tally(name='Dose g avant 1m')
tallyaD1mg.filters = [mesh_a1m_filter,energy_function_filter_g,phot_filter]
tallyaD1mg.scores = ['flux']
tallies.append(tallyaD1mg)


tallyaD1mgr = openmc.Tally(name='Dose g avant 1m R')
tallyaD1mgr.filters = [mesh_filter_r,energy_function_filter_g,phot_filter]
tallyaD1mgr.scores = ['flux']
tallies.append(tallyaD1mgr)

mesh_globalDg = openmc.Tally(name='Dose g global')
mesh_globalDg.filters = [mesh_filter_global,phot_filter,energy_function_filter_g]
mesh_globalDg.scores = ['flux']
tallies.append(mesh_globalDg)


# Export to "tallies.xml"
tallies.export_to_xml()

In [21]:
src = openmc.Source()
src.space=openmc.stats.Point((0.001, 0.001, 150.))

openmc.config['chain_file']='/home/thomas/openmc/xsdir/chain_endfb71_sfr.xml'

energy_dist_g = openmc.data.decay_photon_energy('Co60')

# # case Gamma
src.energy=energy_dist_g
src.strength=1/openmc.data.decay_constant('Co60')
src.particle='photon'


settings = openmc.Settings()
settings.source = src

settings.run_mode='fixed source'

settings.batches = 40000
settings.inactive = 20
settings.particles = 40000
settings.export_to_xml()

In [22]:
openmc.run()



                                %%%%%%%%%%%%%%%
                           %%%%%%%%%%%%%%%%%%%%%%%%
                        %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
                      %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
                    %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
                   %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
                                    %%%%%%%%%%%%%%%%%%%%%%%%
                                     %%%%%%%%%%%%%%%%%%%%%%%%
                 ###############      %%%%%%%%%%%%%%%%%%%%%%%%
                ##################     %%%%%%%%%%%%%%%%%%%%%%%
                ###################     %%%%%%%%%%%%%%%%%%%%%%%
                ####################     %%%%%%%%%%%%%%%%%%%%%%
                #####################     %%%%%%%%%%%%%%%%%%%%%
                ######################     %%%%%%%%%%%%%%%%%%%%
                #######################     %%%%%%%%%%%%%%%%%%
                 #######################     %%%%%%%%%%%%%%%%%
                 #####################